In [49]:
import torch
from torch import nn
from torch import optim
import torch.nn.functional as F
from torchvision import datasets, transforms, models
from torch.utils.data import DataLoader, Dataset

import pandas as pd
import numpy as np

from random import shuffle, seed

In [22]:
# Process original dataset, create windows (60 samples(rows), about 1 second)
first_df = pd.read_csv("./Activity Recognition from Single Chest-Mounted Accelerometer/1.csv")
first_df.columns = ["time", "x_acce", "y_acce", "z_acce", "label"]
first_df = first_df[59:]
data = []
# first_df
window = 1
while window*60 < len(first_df.index):
    data60 = first_df[(window - 1)*60:window*60]
    data.append(data60.values)
    window += 1

len(data)

2707

In [23]:
# delete window if multiple activities presents
cleaned_data = []
for i in data:
    previous_label = -1
    for j in i:
        current_label = j[4]
        if (previous_label != -1) and (current_label != previous_label):
            print("data contains different activities!")
            break
        else:
            previous_label = current_label
    else:
        cleaned_data.append(i)

data contains different activities!
data contains different activities!
data contains different activities!
data contains different activities!
data contains different activities!
data contains different activities!
data contains different activities!
data contains different activities!


In [24]:
len(cleaned_data)

2699

In [25]:
# shuffle the data
seed(101)
shuffle(cleaned_data)
cleaned_data

[array([[8.3700e+04, 1.8930e+03, 2.3830e+03, 1.9810e+03, 7.0000e+00],
        [8.3701e+04, 1.8970e+03, 2.3830e+03, 1.9750e+03, 7.0000e+00],
        [8.3702e+04, 1.8890e+03, 2.3870e+03, 1.9980e+03, 7.0000e+00],
        [8.3703e+04, 1.8960e+03, 2.3890e+03, 2.0120e+03, 7.0000e+00],
        [8.3704e+04, 1.8990e+03, 2.3900e+03, 2.0160e+03, 7.0000e+00],
        [8.3705e+04, 1.8900e+03, 2.3830e+03, 2.0100e+03, 7.0000e+00],
        [8.3706e+04, 1.8870e+03, 2.3820e+03, 2.0230e+03, 7.0000e+00],
        [8.3707e+04, 1.8850e+03, 2.3830e+03, 2.0130e+03, 7.0000e+00],
        [8.3708e+04, 1.9000e+03, 2.3890e+03, 2.0030e+03, 7.0000e+00],
        [8.3709e+04, 1.8970e+03, 2.3780e+03, 2.0050e+03, 7.0000e+00],
        [8.3710e+04, 1.8880e+03, 2.3840e+03, 2.0140e+03, 7.0000e+00],
        [8.3711e+04, 1.8870e+03, 2.3850e+03, 2.0240e+03, 7.0000e+00],
        [8.3712e+04, 1.8910e+03, 2.3910e+03, 2.0180e+03, 7.0000e+00],
        [8.3713e+04, 1.8890e+03, 2.3890e+03, 2.0050e+03, 7.0000e+00],
        [8.3714e+04,

In [26]:
# extract label from each window
labels = []
for i in cleaned_data:
    label = i[0][4]
    labels.append(label)
labels = np.array(labels)
labels

array([7., 1., 7., ..., 7., 4., 7.])

In [88]:
features = []
for i in cleaned_data:
    new = np.delete(i, 4, 1)
    features.append(new)
features = np.array(features)
features

array([[[ 83700.,   1893.,   2383.,   1981.],
        [ 83701.,   1897.,   2383.,   1975.],
        [ 83702.,   1889.,   2387.,   1998.],
        ...,
        [ 83757.,   1921.,   2403.,   1996.],
        [ 83758.,   1918.,   2399.,   1991.],
        [ 83759.,   1918.,   2390.,   2001.]],

       [[ 24600.,   1949.,   2381.,   2100.],
        [ 24601.,   1951.,   2379.,   2095.],
        [ 24602.,   1959.,   2379.,   2091.],
        ...,
        [ 24657.,   1953.,   2384.,   2090.],
        [ 24658.,   1954.,   2386.,   2095.],
        [ 24659.,   1952.,   2382.,   2091.]],

       [[ 89340.,   1862.,   2378.,   1999.],
        [ 89341.,   1869.,   2377.,   1987.],
        [ 89342.,   1879.,   2378.,   1987.],
        ...,
        [ 89397.,   1877.,   2380.,   1978.],
        [ 89398.,   1869.,   2379.,   1985.],
        [ 89399.,   1875.,   2380.,   1988.]],

       ...,

       [[133020.,   1889.,   2385.,   1990.],
        [133020.,   1883.,   2381.,   1994.],
        [133020.,   18

In [89]:
# combine the features and labels, and convert it to a csv
k = list(zip(features, labels))
activity_data = pd.DataFrame(k)
activity_data

0    1
0     [[83700.0, 1893.0, 2383.0, 1981.0], [83701.0, ...  7.0
1     [[24600.0, 1949.0, 2381.0, 2100.0], [24601.0, ...  1.0
2     [[89340.0, 1862.0, 2378.0, 1999.0], [89341.0, ...  7.0
3     [[54780.0, 1914.0, 2250.0, 2013.0], [54781.0, ...  4.0
4     [[123960.0, 1872.0, 2375.0, 2016.0], [123960.0...  7.0
5     [[16860.0, 1981.0, 2374.0, 2126.0], [16861.0, ...  1.0
6     [[81540.0, 1886.0, 2379.0, 2019.0], [81541.0, ...  7.0
7     [[115380.0, 1902.0, 2385.0, 1990.0], [115380.0...  7.0
8     [[55860.0, 1848.0, 2512.0, 1998.0], [55861.0, ...  4.0
9     [[146820.0, 1872.0, 2379.0, 1979.0], [146820.0...  7.0
10    [[98820.0, 1911.0, 2382.0, 1988.0], [98821.0, ...  7.0
11    [[73620.0, 1914.0, 2380.0, 2015.0], [73621.0, ...  3.0
12    [[89520.0, 1876.0, 2383.0, 1985.0], [89521.0, ...  7.0
13    [[3900.0, 1971.0, 2372.0, 2130.0], [3901.0, 19...  1.0
14    [[112860.0, 1902.0, 2382.0, 1976.0], [112860.0...  7.0
15    [[100680.0, 1884.0, 2378.0, 1986.0], [100680.0...  7.0
16    [[153540.0, 1900.0, 2379.0, 2099.0], [153540.0...  7.0
17    [[80760.0, 1924.0, 2380.0, 2018.0], [80761.0, ...  7.0
18    [[106320.0, 1899.0, 2390.0, 1972.0], [106320.0...  7.0
19    [[132660.0, 1893.0, 2388.0, 2007.0], [132660.0...  7.0
20    [[5520.0, 1961.0, 2372.0, 2116.0], [5521.0, 19...  1.0
21    [[125400.0, 1871.0, 2383.0, 2006.0], [125400.0...  7.0
22    [[5940.0, 1963.0, 2379.0, 2111.0], [5941.0, 19...  1.0
23    [[8640.0, 1952.0, 2377.0, 2103.0], [8641.0, 19...  1.0
24    [[155940.0, 1929.0, 2376.0, 2106.0], [155940.0...  7.0
25    [[124440.0, 1881.0, 2373.0, 2013.0], [124440.0...  7.0
26    [[134700.0, 1892.0, 2379.0, 1969.0], [134700.0...  7.0
27    [[29760.0, 1967.0, 2374.0, 2139.0], [29761.0, ...  1.0
28    [[48480.0, 1868.0, 2548.0, 2068.0], [48481.0, ...  4.0
29    [[111180.0, 1905.0, 2380.0, 1974.0], [111180.0...  7.0
...                                                 ...  ...
2669  [[104280.0, 1891.0, 2384.0, 1985.0], [104280.0...  7.0
2670  [[99780.0, 1911.0, 2383.0, 2002.0], [99781.0, ...  7.0
2671  [[157140.0, 1892.0, 2381.0, 2073.0], [157140.0...  7.0
2672  [[58920.0, 1843.0, 2307.0, 1995.0], [58921.0, ...  4.0
2673  [[80640.0, 1904.0, 2373.0, 2056.0], [80641.0, ...  7.0
2674  [[116460.0, 1910.0, 2388.0, 1981.0], [116460.0...  7.0
2675  [[47280.0, 1892.0, 2370.0, 2073.0], [47281.0, ...  4.0
2676  [[90600.0, 1876.0, 2391.0, 1994.0], [90601.0, ...  7.0
2677  [[132540.0, 1904.0, 2382.0, 2018.0], [132540.0...  7.0
2678  [[109920.0, 1909.0, 2385.0, 1976.0], [109920.0...  7.0
2679  [[21840.0, 1963.0, 2370.0, 2113.0], [21841.0, ...  1.0
2680  [[39780.0, 1914.0, 2491.0, 2034.0], [39781.0, ...  4.0
2681  [[47700.0, 1934.0, 2331.0, 2055.0], [47701.0, ...  4.0
2682  [[62940.0, 1891.0, 2300.0, 2007.0], [62941.0, ...  4.0
2683  [[17340.0, 1981.0, 2375.0, 2130.0], [17341.0, ...  1.0
2684  [[108120.0, 1914.0, 2380.0, 1974.0], [108120.0...  7.0
2685  [[81360.0, 1912.0, 2357.0, 2112.0], [81361.0, ...  7.0
2686  [[52380.0, 1879.0, 2327.0, 2046.0], [52381.0, ...  4.0
2687  [[119820.0, 1887.0, 2383.0, 1996.0], [119820.0...  7.0
2688  [[71220.0, 1987.0, 2304.0, 2252.0], [71221.0, ...  5.0
2689  [[54720.0, 1825.0, 2581.0, 1980.0], [54721.0, ...  4.0
2690  [[148440.0, 1903.0, 2390.0, 2032.0], [148440.0...  7.0
2691  [[52920.0, 1922.0, 2398.0, 2021.0], [52921.0, ...  4.0
2692  [[124260.0, 1873.0, 2382.0, 2003.0], [124260.0...  7.0
2693  [[11940.0, 1958.0, 2380.0, 2113.0], [11941.0, ...  1.0
2694  [[115320.0, 1907.0, 2390.0, 1995.0], [115320.0...  7.0
2695  [[88680.0, 1879.0, 2379.0, 1989.0], [88681.0, ...  7.0
2696  [[133020.0, 1889.0, 2385.0, 1990.0], [133020.0...  7.0
2697  [[48060.0, 1882.0, 2511.0, 2148.0], [48061.0, ...  4.0
2698  [[143340.0, 1904.0, 2387.0, 1980.0], [143340.0...  7.0

[2699 rows x 2 columns]

In [90]:
# split the data to test and train
activity_data.columns = ["features", "labels"]
activity_data_train = activity_data[:int(len(activity_data)*0.7)]
activity_data_test = activity_data[int(len(activity_data)*0.7):]
activity_data_train.to_csv("./activity_data_train.csv", encoding='utf-8-sig')
activity_data_train.to_csv("./activity_data_test.csv", encoding='utf-8-sig')

In [109]:
kk = pd.read_csv("./activity_data_train.csv")
o = kk["features"]
print(type(o))
#print(type(activity_data_train["features"][0]))

<class 'pandas.core.series.Series'>


In [305]:
# define our dataset in pytorch
class DatasetHAR(Dataset):
    
    def __init__(self, file, transform=None):
        #self.data = pd.read_csv(file_path)
        self.data = file
        self.transform = transform
        
    def __len__(self):
        return len(self.data)
    
    def __getitem__(self, index):
        # load image as ndarray type (Height * Width * Channels)
        # be carefull for converting dtype to np.uint8 [Unsigned integer (0 to 255)]
        # in this example, i don't use ToTensor() method of torchvision.transforms
        # so you can convert numpy ndarray shape to tensor in PyTorch (H, W, C) --> (C, H, W)
        
        features = torch.tensor(self.data["features"].iloc[index])
        features = features.view(60, 1, 4)
        labels = torch.tensor(self.data["labels"].iloc[index], dtype=torch.long)
        #print(labels.type())
        
#         if self.transform is not None:
#             image = self.transform(image)
            
        return features, labels

In [306]:
# construct training and testing dataset in csv
# train_dataset = DatasetHAR("./activity_data_train.csv")
# test_dataset = DatasetHAR("./activity_data_test.csv")
train_dataset = DatasetHAR(activity_data_train)
test_dataset = DatasetHAR(activity_data_test)
feature, label = train_dataset.__getitem__(0)
feature

tensor([[[83700.,  1893.,  2383.,  1981.]],

        [[83701.,  1897.,  2383.,  1975.]],

        [[83702.,  1889.,  2387.,  1998.]],

        [[83703.,  1896.,  2389.,  2012.]],

        [[83704.,  1899.,  2390.,  2016.]],

        [[83705.,  1890.,  2383.,  2010.]],

        [[83706.,  1887.,  2382.,  2023.]],

        [[83707.,  1885.,  2383.,  2013.]],

        [[83708.,  1900.,  2389.,  2003.]],

        [[83709.,  1897.,  2378.,  2005.]],

        [[83710.,  1888.,  2384.,  2014.]],

        [[83711.,  1887.,  2385.,  2024.]],

        [[83712.,  1891.,  2391.,  2018.]],

        [[83713.,  1889.,  2389.,  2005.]],

        [[83714.,  1883.,  2389.,  2003.]],

        [[83715.,  1880.,  2386.,  2015.]],

        [[83716.,  1875.,  2398.,  2026.]],

        [[83717.,  1880.,  2402.,  2040.]],

        [[83718.,  1890.,  2401.,  2013.]],

        [[83719.,  1898.,  2398.,  2004.]],

        [[83720.,  1906.,  2379.,  2009.]],

        [[83721.,  1892.,  2385.,  2018.]],

        [[

In [307]:
# load data
trainloader = DataLoader(train_dataset, batch_size=64)
testloader = DataLoader(test_dataset, batch_size=64)

In [297]:
model = models.resnet18(pretrained=False)
model.conv1 = torch.nn.Conv2d(60, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
model.fc = torch.nn.Linear(512, 8, bias=True)
model = model.double()
model

ResNet(
  (conv1): Conv2d(4, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (1): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace)
      (conv2): Co

In [298]:
criterion = nn.NLLLoss()
optimizer = optim.Adam(model.parameters(), lr=0.003)

epochs = 30
steps = 0

train_losses, test_losses = [], []
for e in range(epochs):
    running_loss = 0
    for feature, label in trainloader:
        
        optimizer.zero_grad()
        
        log_ps = model(feature)
        loss = criterion(log_ps, label)
        loss.backward()
        optimizer.step()
        
        running_loss += loss.item()
        #print(running_loss)
        
    else:
        test_loss = 0
        accuracy = 0
        
        # Turn off gradients for validation, saves memory and computations
        with torch.no_grad():
            for feature, label in testloader:
                log_ps = model(feature)
                test_loss += criterion(log_ps, label)
                
                ps = torch.exp(log_ps)
                top_p, top_class = ps.topk(1, dim=1)
                equals = top_class == label.view(*top_class.shape)
                accuracy += torch.mean(equals.type(torch.FloatTensor))
                
        train_losses.append(running_loss/len(trainloader))
        test_losses.append(test_loss/len(testloader))

        print("Epoch: {}/{}.. ".format(e+1, epochs),
              "Training Loss: {:.3f}.. ".format(running_loss/len(trainloader)),
              "Test Loss: {:.3f}.. ".format(test_loss/len(testloader)),
              "Test Accuracy: {:.3f}".format(accuracy/len(testloader)))

Epoch: 1/30..  Training Loss: -41.661..  Test Loss: -85.617..  Test Accuracy: 0.857
Epoch: 2/30..  Training Loss: -134.724..  Test Loss: -197.029..  Test Accuracy: 0.848


KeyboardInterrupt: 

In [345]:
# define our dataset in pytorch
class DatasetH(Dataset):
    
    def __init__(self, file, transform=None):
        #self.data = pd.read_csv(file_path)
        self.data = file
        self.transform = transform
        
    def __len__(self):
        return len(self.data)
    
    def __getitem__(self, index):
        # load image as ndarray type (Height * Width * Channels)
        # be carefull for converting dtype to np.uint8 [Unsigned integer (0 to 255)]
        # in this example, i don't use ToTensor() method of torchvision.transforms
        # so you can convert numpy ndarray shape to tensor in PyTorch (H, W, C) --> (C, H, W)
        
        features = torch.tensor(self.data["features"].iloc[index])
        labels = torch.tensor(self.data["labels"].iloc[index], dtype=torch.long)
        #print(labels.type())
        
#         if self.transform is not None:
#             image = self.transform(image)
            
        return features, labels

In [347]:
train_dataset2 = DatasetH(activity_data_train)
test_dataset2 = DatasetH(activity_data_test)
feature, label = train_dataset.__getitem__(0)
feature.shape

torch.Size([60, 1, 4])

In [348]:
# load data
trainloader2 = DataLoader(train_dataset2, batch_size=64)
testloader2 = DataLoader(test_dataset2, batch_size=64)

In [349]:
model2 = nn.Sequential(nn.Linear(240, 128),
                      nn.ReLU(),
                      nn.Linear(128, 64),
                      nn.ReLU(),
                      nn.Linear(64, 8))
model2 = model2.double()

In [350]:
# Test
criterion = nn.NLLLoss()
optimizer = optim.Adam(model.parameters(), lr=0.003)

epochs = 30
steps = 0

train_losses, test_losses = [], []
for e in range(epochs):
    running_loss = 0
    for feature, label in trainloader:
        feature = feature.view(feature.shape[0], -1)
        optimizer.zero_grad()
        
        log_ps = model2(feature)
        loss = criterion(log_ps, label)
        loss.backward()
        optimizer.step()
        
        running_loss += loss.item()
        #print(running_loss)
    else:
        test_loss = 0
        accuracy = 0

        # Turn off gradients for validation, saves memory and computations
        with torch.no_grad():
            for feature, label in testloader2:
                feature = feature.view(feature.shape[0], -1)
                #print(feature.shape)
                #print(feature.shape)
                #print(label.shape)
                log_ps = model2(feature)
                test_loss += criterion(log_ps, label)

                ps = torch.exp(log_ps)
                top_p, top_class = ps.topk(1, dim=1)
                equals = top_class == label.view(*top_class.shape)
                accuracy += torch.mean(equals.type(torch.FloatTensor))

        train_losses.append(running_loss/len(trainloader))
        test_losses.append(test_loss/len(testloader))

        print("Test Loss: {:.3f}.. ".format(test_loss/len(testloader)),
              "Test Accuracy: {:.3f}".format(accuracy/len(testloader)))

Test Loss: -5211.037..  Test Accuracy: 0.551
Test Loss: -5211.037..  Test Accuracy: 0.551
Test Loss: -5211.037..  Test Accuracy: 0.551
Test Loss: -5211.037..  Test Accuracy: 0.551
Test Loss: -5211.037..  Test Accuracy: 0.551
Test Loss: -5211.037..  Test Accuracy: 0.551
Test Loss: -5211.037..  Test Accuracy: 0.551
Test Loss: -5211.037..  Test Accuracy: 0.551
Test Loss: -5211.037..  Test Accuracy: 0.551
Test Loss: -5211.037..  Test Accuracy: 0.551


KeyboardInterrupt: 